# **Build land and ocean tiles from Google Earth Engine**


### **Install Earth Engine API**

In [ ]:
!pip install earthengine-api --upgrade

### **Install Folium**

In [ ]:
!pip install folium

### **Prevent re-import errors**

In [1]:
%load_ext autoreload
%autoreload 2

### **Imports**

In [3]:
from IPython.core.display import display
import numpy as np
import folium
import ast
import ee

### **Sign-in to Google Earth Engine**

In [3]:
ee.Authenticate()
try:
  ee.Initialize()
  print("Earth Engine initilized successfully!")
except ee.EEException as e:
  print("Earth Engine could not be initialized!")


Successfully saved authorization token.
Earth Engine initilized successfully!


## **Download Tiled California Data**

### **Find proportion of tile area that is water**

In [ ]:
def getProportionWater(waterImage, sw_longitude, sw_latitude, side=0.1):
    region = ee.Geometry.BBox(sw_longitude, sw_latitude, 
                              sw_longitude+side, sw_latitude+side)
    waterDictionary = waterImage.reduceRegion(
        reducer= ee.Reducer.mean(),
        geometry= region,
        scale= 250,
        maxPixels= 1e9)
    return waterDictionary.getInfo()['water_mask']

# get land mask, 
dataset = ee.Image('MODIS/MOD44W/MOD44W_005_2000_02_24')
waterMask = dataset.select('water_mask')
# water pixel == 1
# land pixel == 0

# southwest(long,lat), northeast(long,lat)
sf_water = getProportionWater(waterMask, -122.6, 37.55, 0.5)
sc_water = getProportionWater(waterMask,-122, 36.2, 1)
ocean_water = getProportionWater(waterMask,-124, 33, 1)

print(f"San Francisco Bounding Box contains {sf_water*100:0.0f}% water")
print(f"Santa Cruz Bounding Box contains {sc_water*100:0.0f}% water")
print(f"Ocean Bounding Box contains {ocean_water*100:0.0f}% water")

### **Collect water proportion across all tiles**

In [42]:
# create a bounding box tiling over California
# get land data
southwest=[32.8, -124.2]
northeast=[42.0, -114.4]
side=0.1

latitudes = np.arange(southwest[0], northeast[0]-side, side)
longitudes = np.arange(southwest[1], northeast[1]-side, side)

#land mask
dataset = ee.Image('MODIS/MOD44W/MOD44W_005_2000_02_24')
waterMask = dataset.select('water_mask')

tiles = []
finished = 0
total = len(longitudes) * len(latitudes)

#start south, step north by 0.1 lat
for latitude in latitudes:
    #start west, step east by 0.1 long
    for longitude in longitudes:
        waterProp = getProportionWater(waterMask, longitude, latitude, side)
        tiles.append([(longitude, latitude), waterProp])
        finished += 1
        print(f'\r{finished:04}/{total}', end ='')
print('\nAll tiles found')


9016/9016
All tiles found


### **Split into All|Land|Water and save to data directory**

In [51]:
# tile must be less than 50% water
tolerance = 0.50
allTiles = [[(np.round(tile[0][0],1), np.round(tile[0][1],1)), np.round(tile[1],3)] for tile in tiles]
landTiles = [tile for tile in allTiles if tile[1] < tolerance]
waterTiles =[tile for tile in allTiles if tile[1] >= tolerance]

with open('../data/tiles/allTiles.txt', 'w') as file:
    for tile in allTiles:
        file.write(f'({tile[0][0]}, {tile[0][1]}), {tile[1]}\n')
    print('data/tiles/allTiles.txt - Complete')

with open('../data/tiles/landTiles.txt', 'w') as file:
    for tile in landTiles:
        file.write(f'({tile[0][0]}, {tile[0][1]}), {tile[1]}\n')
    print('data/tiles/landTiles.txt - Complete')

with open('../data/tiles/waterTiles.txt', 'w') as file:
    for tile in waterTiles:
        file.write(f'({tile[0][0]}, {tile[0][1]}), {tile[1]}\n')
    print('data/tiles/waterTiles.txt - Complete')


data/allTiles.txt - Complete
data/landTiles.txt - Complete
data/waterTiles.txt - Complete


### **Read from data directory**

In [5]:
allTiles = []
with open('../data/tiles/allTiles.txt', 'r') as file:
    for line in file.readlines():
        allTiles.append(ast.literal_eval(line))

landTiles = []
with open('../data/tiles/landTiles.txt', 'r') as file:
    for line in file.readlines():
        landTiles.append(ast.literal_eval(line))

waterTiles = []
with open('../data/tiles/waterTiles.txt', 'r') as file:
    for line in file.readlines():
        waterTiles.append(ast.literal_eval(line))

print(len(allTiles), len(landTiles), len(waterTiles))

9016 6910 2106


### **Build the land vs sea map**

In [10]:
tile = {'tile':'https://stamen-tiles-{s}.a.ssl.fastly.net/terrain-background/{z}/{x}/{y}{r}.png',
                'attr': 'Map tiles by <a href="http://stamen.com">Stamen Design</a>, <a href="http://creativecommons.org/licenses/by/3.0">CC BY 3.0</a> &mdash; Map data &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors'}

# Build map from selected tile type
fMap = folium.Map(location=[37.5010, -122.1899], zoom_start=10,
                    tiles = tile['tile'],
                    attr = tile['attr'])
for box in allTiles:
    sw_long = box[0][0]
    sw_lat  = box[0][1]
    water   = box[1]

    if water < 0.5:
        folium.Rectangle(
            bounds=[(sw_lat, sw_long), (sw_lat+0.1, sw_long+0.1)],
            color='#00FF00',
            fill=True,
            fill_color='#00FF00',
            fill_opacity=0.2
        ).add_to(fMap)
    else:
        folium.Rectangle(
            bounds=[(sw_lat, sw_long), (sw_lat+0.1, sw_long+0.1)],
            color='#0000FF',
            fill=True,
            fill_color='#0000FF',
            fill_opacity=0.2
        ).add_to(fMap)

### **Visualize and save**

In [11]:
display(fMap)
fMap.save('../outputs/landVsSeaTiles.html')